### Inicializar paquetes

In [8]:
import os
os.environ['KMP_DUPLICATE_LIB_OK']='True'
import cv2  
import math 
from ultralytics import YOLO
from collections import defaultdict
import numpy as np
import easyocr
import csv

### Entrenamiento del modelo

In [ ]:
model = YOLO('yolov8n.pt')

# Entrenar el modelo
model.train(
    data='license_plates.yaml',  # El archivo de configuración YAML
    epochs=50,  # Ajusta el número de épocas según sea necesario
    imgsz=500,  # Tamaño de las imágenes (puedes ajustarlo)
    batch=15,   # Tamaño del batch
    device='0'    # entrenar con GPU
)
model.val()

### Detección a tiempo real

In [ ]:
# Carga del modelo YOLO para la detección general de objetos
yolo11 = YOLO('yolo11n.pt')

# Carga del modelo YOLO entrenado para detectar matrículas
license_plates_model = YOLO('model\\weights\\best.pt')

# Carga del modelo para reconocimiento de texto
reader = easyocr.Reader(['es'])

# Etiquetas de las clases del modelo de detección general
classNames = ["person", "bicycle", "car", "motorbike", "aeroplane", "bus", "train", "truck"]

filename = "C0142.MP4"
vid = cv2.VideoCapture(filename)

# Bucle que trata fotograma a fotograma
while True:
    ret, frame = vid.read()

    if not ret:
        break

    # Detección general
    results = yolo11.track(frame, persist=True, classes=[0, 2, 3, 5, 7])

    if results is not None:
        # Procesamos cada detección
        for r in results:
            boxes = r.boxes

            for box in boxes:
                # Coordenadas del contenedor detectado
                x1, y1, x2, y2 = map(int, box.xyxy[0])

                #Etiqueta de seguimiento
                if box.id is not None:
                    track_id = str(int(box.id[0].tolist()))
                else:
                    track_id = ''
                
                # Confianza
                confidence = math.ceil((box.conf[0]*100))/100

                # Clase
                cls = int(box.cls[0])

                # Convierte identificador numérico de clase a un color RGB
                escala = int((cls / len(classNames)) * 255 * 3)
                if escala >= 255*2:
                    R = 255
                    G = 255
                    B = escala - 255*2
                else:
                    if escala >= 255:
                        R = 255
                        G = escala - 255
                        B = 0
                    else:
                        R = escala
                        G = 0
                        B = 0

                # Dibuja el recuadro para el objeto detectado
                cv2.rectangle(frame, (x1, y1), (x2, y2), (255, 0, 0), 3)
                cv2.putText(frame, track_id + ' ' + classNames[cls] , [x1, y1], cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 0, B), 2)


                # Recorta el objeto de interés para buscar la matrícula
                objeto_interes = frame[y1:y2, x1:x2]
                
                # Detección de matrículas dentro del objeto de interés
                plate_results = license_plates_model(objeto_interes)
                
                for plate_result in plate_results:
                    plate_boxes = plate_result.boxes
                    
                    for plate_box in plate_boxes:
                        # Coordenadas de la matrícula
                        px1, py1, px2, py2 = map(int, plate_box.xyxy[0])
                        
                        global_x1 = x1 + px1
                        global_y1 = y1 + py1
                        global_x2 = x1 + px2
                        global_y2 = y1 + py2
                        
                        # Dibuja el recuadro para la matrícula detectada
                        cv2.rectangle(frame, (global_x1, global_y1), (global_x2, global_y2), (0, 255, 0), 2)
                        
                        # Recorta la región de la matrícula para leer el texto
                        placa_img = frame[global_y1:global_y2, global_x1:global_x2]
                        
                        # Leer el texto de la matrícula
                        result_ocr = reader.readtext(placa_img, allowlist='0123456789ABCDEFGHIJKLMNOPQRSTUVWXYZ')

                        for (bbox, text, prob) in result_ocr:
                            print(f"Texto detectado: {text} con una probabilidad de {prob:.2f}")
                            cv2.putText(frame, text, (global_x1, global_y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (36, 255, 12), 2)

        cv2.imshow("Detección YOLO y OCR", frame)

        # Detener si se presiona la tecla "q"
        if cv2.waitKey(1) & 0xFF == ord("q"):
            break

    # Detener el bucle si se presiona ESC
    if cv2.waitKey(20) == 27:
        break

vid.release()
cv2.destroyAllWindows()



0: 384x640 4 cars, 1 bus, 11.2ms
Speed: 0.0ms preprocess, 11.2ms inference, 1.0ms postprocess per image at shape (1, 3, 384, 640)

0: 448x512 (no detections), 7.7ms
Speed: 0.0ms preprocess, 7.7ms inference, 0.0ms postprocess per image at shape (1, 3, 448, 512)

0: 416x512 (no detections), 0.8ms
Speed: 3.6ms preprocess, 0.8ms inference, 0.0ms postprocess per image at shape (1, 3, 416, 512)

0: 320x512 (no detections), 7.0ms
Speed: 5.8ms preprocess, 7.0ms inference, 1.0ms postprocess per image at shape (1, 3, 320, 512)

0: 352x512 (no detections), 4.1ms
Speed: 1.1ms preprocess, 4.1ms inference, 0.0ms postprocess per image at shape (1, 3, 352, 512)

0: 384x512 (no detections), 4.7ms
Speed: 0.0ms preprocess, 4.7ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 512)

0: 384x640 4 cars, 1 bus, 0.0ms
Speed: 0.0ms preprocess, 0.0ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 640)

0: 416x512 (no detections), 0.0ms
Speed: 0.0ms preprocess, 0.0ms inference, 0.0ms po

### Reconocimiento de vehiculos y matrículas (Con su texto)

In [ ]:
# Función para añadir líneas al archivo CSV
def addLineToCSV(
    frame_count: int, 
    class_name: str, 
    confidence: float, 
    track_id: int, 
    x1: int, 
    y1: int, 
    x2: int, 
    y2: int, 
    matricula: str = "", 
    m_confidence: str = "", 
    m_x1: str = "", 
    m_y1: str = "", 
    m_x2: str = "", 
    m_y2: str = "", 
    texto_matricula: str = ""
):
    with open('output.csv', mode='a', newline='') as file:
        writer = csv.writer(file)
        writer.writerow([
            frame_count, 
            class_name, 
            confidence, 
            track_id, 
            x1, 
            y1, 
            x2, 
            y2, 
            matricula, 
            m_confidence, 
            m_x1, 
            m_y1, 
            m_x2, 
            m_y2, 
            texto_matricula
        ])

In [ ]:

# Carga del modelo YOLO para detección general de objetos
yolo11 = YOLO('yolo11n.pt')

# Carga del modelo YOLO entrenado para detectar matrículas
license_plates_model = YOLO('model\\weights\\best.pt')

# Carga del modelo para reconocimiento de texto en español
reader = easyocr.Reader(['es'])

# Etiquetas de las clases del modelo de detección general
classNames = ["person", "bicycle", "car", "motorbike", "aeroplane", "bus", "train", "truck"]

filename = "C0142.MP4"
vid = cv2.VideoCapture(filename)

frame_width = int(vid.get(3))
frame_height = int(vid.get(4))
fps = vid.get(cv2.CAP_PROP_FPS)

# Inicializamos el VideoWriter para guardar el video
output_filename = 'video_anotado.mp4'
fourcc = cv2.VideoWriter_fourcc(*'mp4v')
out = cv2.VideoWriter(output_filename, fourcc, fps, (frame_width, frame_height))

frame_count = 0

try:
    while vid.isOpened():
        ret, frame = vid.read()

        if not ret:
            break
        
        frame_count+=1

        # Detección general
        results = yolo11.track(frame, persist=True, classes=[0, 2, 3, 5, 7])

        if results:
            for result in results:
                boxes = result.boxes
                for box in boxes:
                    # Coordenadas del contenedor detectado
                    x1, y1, x2, y2 = map(int, box.xyxy[0])
                    
                    #Etiqueta de seguimiento
                    if box.id is not None:
                        track_id = str(int(box.id[0].tolist()))
                    else:
                        track_id = ''
                    
                    # Confianza
                    confidence = math.ceil((box.conf[0]*100))/100
                    #print("Confianza --->",confidence)

                    # Clase
                    cls = int(box.cls[0])
                    #print("Clase -->", classNames[cls])

                    # Convierte identificador numérico de clase a un color RGB
                    escala = int((cls / len(classNames)) * 255 * 3)
                    if escala >= 255*2:
                        R = 255
                        G = 255
                        B = escala - 255*2
                    else:
                        if escala >= 255:
                            R = 255
                            G = escala - 255
                            B = 0
                        else:
                            R = escala
                            G = 0
                            B = 0

                    # Dibuja el contenedor para el objeto detectado
                    cv2.rectangle(frame, (x1, y1), (x2, y2), (255, 0, 0), 3)
                    cv2.putText(frame, track_id + ' ' + classNames[cls] , [x1, y1], cv2.FONT_HERSHEY_SIMPLEX, 1, (255, 0, B), 2)

                    # Recorta el objeto de interés para buscar la matrícula
                    objeto_interes = frame[y1:y2, x1:x2] 

                    # Detección de matrículas dentro del vehículo
                    plate_results = license_plates_model(objeto_interes)

                    # Si no tiene matrícula comenta en output.csv
                    if not plate_results[0].boxes:
                        addLineToCSV(frame_count, classNames[cls], confidence, track_id, x1, y1, x2, y2)
                        

                    for plate_result in plate_results:
                        plate_boxes = plate_result.boxes
                        for plate_box in plate_boxes:

                            px1, py1, px2, py2 = map(int, plate_box.xyxy[0])
                            
                            global_x1 = x1 + px1
                            global_y1 = y1 + py1
                            global_x2 = x1 + px2
                            global_y2 = y1 + py2

                            # Dibujar la caja alrededor de la matrícula
                            cv2.rectangle(frame, (global_x1, global_y1), (global_x2, global_y2), (0, 255, 0), 2)

                            # Recortar la región de la matrícula
                            placa_img = frame[global_y1:global_y2, global_x1:global_x2]

                            # Leer el texto de la matrícula
                            result_ocr = reader.readtext(placa_img, allowlist='0123456789ABCDEFGHIJKLMNOPQRSTUVWXYZ')

                            if not (result_ocr): 
                                addLineToCSV(frame_count, classNames[cls], confidence, track_id, x1, y1, x2, y2, matricula=True, m_x1=global_x1, m_y1=global_y1, m_x2=global_x2, m_y2=global_y2)

                            for (bbox, text, prob) in result_ocr:
                                print(f"Texto detectado: {text} con una probabilidad de {prob:.2f}")
                                cv2.putText(frame, text, (global_x1, global_y1 - 10), cv2.FONT_HERSHEY_SIMPLEX, 0.9, (36, 255, 12), 2)
                                
                                addLineToCSV(frame_count, classNames[cls], confidence, track_id, x1, y1, x2, y2, matricula=True, m_x1=global_x1, m_y1=global_y1, m_x2=global_x2, m_y2=global_y2, texto_matricula=text)

        out.write(frame)

    # Liberar recursos
    vid.release()
    out.release()
    cv2.destroyAllWindows()
except KeyboardInterrupt:
    print("Interrupción manual detectada.")
finally:
    # Liberar recursos
    vid.release()
    out.release()
    cv2.destroyAllWindows()



0: 384x640 4 cars, 1 bus, 24.2ms
Speed: 0.0ms preprocess, 24.2ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 640)

0: 448x512 (no detections), 7.7ms
Speed: 6.0ms preprocess, 7.7ms inference, 0.0ms postprocess per image at shape (1, 3, 448, 512)

0: 416x512 (no detections), 8.0ms
Speed: 5.3ms preprocess, 8.0ms inference, 1.0ms postprocess per image at shape (1, 3, 416, 512)

0: 320x512 (no detections), 7.0ms
Speed: 0.1ms preprocess, 7.0ms inference, 0.4ms postprocess per image at shape (1, 3, 320, 512)

0: 352x512 (no detections), 7.9ms
Speed: 0.0ms preprocess, 7.9ms inference, 0.0ms postprocess per image at shape (1, 3, 352, 512)

0: 384x512 (no detections), 7.2ms
Speed: 1.0ms preprocess, 7.2ms inference, 0.0ms postprocess per image at shape (1, 3, 384, 512)

0: 384x640 4 cars, 1 bus, 4.7ms
Speed: 1.9ms preprocess, 4.7ms inference, 4.5ms postprocess per image at shape (1, 3, 384, 640)

0: 416x512 (no detections), 6.1ms
Speed: 0.0ms preprocess, 6.1ms inference, 5.8ms po